In [1]:
# python default library
import os
import shutil
import datetime
import sys
import pickle

# general analysis tool-kit
import numpy as np
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt

# pytorch
import torch
from torch import optim, nn
from torch.utils.tensorboard import SummaryWriter

from torchsummary import summary

# etc
import yaml
yaml.warnings({'YAMLLoadWarning': False})
import mlflow
from collections import defaultdict
from scipy.stats import zscore

# original library

import common as com
import pytorch_modeler as modeler
from pytorch_model import LSTM_AutoEncoder as Model
from pytorch_utils import filtered_load_model
import models

import librosa
import IPython
import librosa.display

In [2]:
with open("./config.yaml", 'rb') as f:
    config = yaml.load(f)

#log_folder = config['IO_OPTION']['OUTPUT_ROOT']+'/{0}.log'.format(datetime.date.today())
#logger = com.setup_logger(log_folder, '00_train.py')

/home/hiroki/anaconda3/lib/python3.7/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


In [3]:
# Setting seed
modeler.set_seed(42)

In [4]:
############################################################################
# Setting I/O path
############################################################################
# input dirs
"""
INPUT_ROOT = config['IO_OPTION']['INPUT_ROOT']
dev_path = INPUT_ROOT + "/dev_data"
add_dev_path = INPUT_ROOT + "/add_dev_data"
# machine type
MACHINE_TYPE = config['IO_OPTION']['MACHINE_TYPE']
machine_types = os.listdir(dev_path)
# output dirs
OUTPUT_ROOT = config['IO_OPTION']['OUTPUT_ROOT']
MODEL_DIR = config['IO_OPTION']['OUTPUT_ROOT'] + '/models'
TB_DIR = config['IO_OPTION']['OUTPUT_ROOT'] + '/tb'
PKL_DIR = OUTPUT_ROOT + '/pkl'
os.makedirs(MODEL_DIR, exist_ok=True)
os.makedirs(TB_DIR, exist_ok=True)
"""

'\nINPUT_ROOT = config[\'IO_OPTION\'][\'INPUT_ROOT\']\ndev_path = INPUT_ROOT + "/dev_data"\nadd_dev_path = INPUT_ROOT + "/add_dev_data"\n# machine type\nMACHINE_TYPE = config[\'IO_OPTION\'][\'MACHINE_TYPE\']\nmachine_types = os.listdir(dev_path)\n# output dirs\nOUTPUT_ROOT = config[\'IO_OPTION\'][\'OUTPUT_ROOT\']\nMODEL_DIR = config[\'IO_OPTION\'][\'OUTPUT_ROOT\'] + \'/models\'\nTB_DIR = config[\'IO_OPTION\'][\'OUTPUT_ROOT\'] + \'/tb\'\nPKL_DIR = OUTPUT_ROOT + \'/pkl\'\nos.makedirs(MODEL_DIR, exist_ok=True)\nos.makedirs(TB_DIR, exist_ok=True)\n'

In [5]:
path = '/media/hiroki/working/research/dcase2020/datasets/DCASE2/dev_data/fan/train/normal_id_00_00000000.wav'
sound_data = com.file_load(path,
                           sr=config['preprocessing']['sample_rate'],
                           mono=config['preprocessing']['mono'])

In [6]:
net = Model(sample_rate=config['preprocessing']['sample_rate'],
            window_size=config['preprocessing']['window_size'],
            hop_size=config['preprocessing']['hop_size'],
            mel_bins=config['preprocessing']['mel_bins'],
            batch_size=1)

/home/hiroki/anaconda3/lib/python3.7/site-packages/librosa/filters.py:235: UserWarning: Empty filters detected in mel frequency basis. Some channels will produce empty responses. Try increasing your sampling rate (and fmax) or reducing n_mels.
  warnings.warn('Empty filters detected in mel frequency basis. '


In [9]:
writer = SummaryWriter()
writer.add_graph(net, torch.from_numpy(sound_data[0]).float())
writer.close()

Tracer cannot infer type of (0.0034484863, 0.008911133, 0.009674072, 0.011077881, 0.014373779, 0.016143799, 0.019042969, 0.0113220215, 0.017730713, 0.012969971, 0.006439209, 0.0072021484, 0.0067749023, 0.009521484, 0.0059814453, 0.009124756, 0.013061523, -0.0033569336, 0.012878418, 0.0074157715, 0.009094238, 0.019561768, 0.00881958, 0.010986328, 0.0074157715, 0.0012512207, 0.0031738281, -0.007232666, -0.0073547363, -0.014526367, -0.0025939941, -0.00061035156, -0.0038757324, 0.0054016113, -0.0050354004, -0.0058288574, -0.0048217773, -0.007537842, -0.004272461, -0.0009765625, -0.01071167, -0.0038452148, -0.0016784668, -0.0029907227, -0.0011291504, -0.0035095215, 0.0004272461, -0.0022888184, 0.0043945312, 0.0010986328, 0.010375977, 0.013183594, 0.015899658, 0.010467529, 0.0052490234, 0.0050964355, 0.00045776367, 0.004058838, 0.003479004, 0.00680542, 0.0053710938, 0.0031433105, -0.007659912, 0.002746582, -0.003540039, -0.0051574707, -0.0015258789, 0.00061035156, -0.0022583008, -0.003112793

/home/hiroki/anaconda3/lib/python3.7/site-packages/ipykernel/ipkernel.py:287: DeprecationWarning: `should_run_async` will not call `transform_cell` automatically in the future. Please pass the result to `transformed_cell` argument and any exception that happen during thetransform in `preprocessing_exc_tuple` in IPython 7.17 and above.
  and should_run_async(code)


RuntimeError: Tracer cannot infer type of (0.0034484863, 0.008911133, 0.009674072, 0.011077881, 0.014373779, 0.016143799, 0.019042969, 0.0113220215, 0.017730713, 0.012969971, 0.006439209, 0.0072021484, 0.0067749023, 0.009521484, 0.0059814453, 0.009124756, 0.013061523, -0.0033569336, 0.012878418, 0.0074157715, 0.009094238, 0.019561768, 0.00881958, 0.010986328, 0.0074157715, 0.0012512207, 0.0031738281, -0.007232666, -0.0073547363, -0.014526367, -0.0025939941, -0.00061035156, -0.0038757324, 0.0054016113, -0.0050354004, -0.0058288574, -0.0048217773, -0.007537842, -0.004272461, -0.0009765625, -0.01071167, -0.0038452148, -0.0016784668, -0.0029907227, -0.0011291504, -0.0035095215, 0.0004272461, -0.0022888184, 0.0043945312, 0.0010986328, 0.010375977, 0.013183594, 0.015899658, 0.010467529, 0.0052490234, 0.0050964355, 0.00045776367, 0.004058838, 0.003479004, 0.00680542, 0.0053710938, 0.0031433105, -0.007659912, 0.002746582, -0.003540039, -0.0051574707, -0.0015258789, 0.00061035156, -0.0022583008

In [7]:
from torchsummary import summary
net = net.to('cuda:0')
summary(net, (sound_data[1],)) # summary(model,(channels,H,W))

torch.Size([2, 1, 129, 128])
torch.Size([2, 129, 128])


AttributeError: 'tuple' object has no attribute 'size'